# Notebook 02 and 03 - Noise Analysis and eV conversion

In [3]:
#Imports 
%matplotlib qt

import hyperspy.api as hs
import numpy as np
import matplotlib.pyplot as plt

from matplotlib.colors import SymLogNorm
from scipy.stats import chi2

In [4]:
#Helper functions for statistical analysis
def hist_var(n,mids,minpoints=5) -> np.float:
    """Helper function to compute sample variance from a 1d histogram"""
    if n.sum()>=minpoints:
        mean = np.average(mids, weights=n)
        var = np.average((mids - mean)**2, weights=n)
    else:
        var = np.nan
        
    return var

def lo_conf_int(var,npts,alpha=0.025) -> float:
    """Helper function to compute the lower confidence interval using chi squared distribution"""
    return (npts-1)*var/chi2.ppf(1-alpha/2,npts)

def hi_conf_int(var,npts,alpha=0.025) -> float:
    """Helper function to compute the higher confidence interval using chi squared distribution"""
    return (npts-1)*var/chi2.ppf(alpha/2,npts)

def hist_var_confint(n,mids,alpha=0.025,minpoints=5) -> np.array([float,float]):
    """Helper function to compute the complete confidence interval using chi squared distribution"""
    var = hist_var(n,mids,minpoints)
    npts = n.sum()
    return np.array([lo_conf_int(var,npts,alpha),hi_conf_int(var,npts,alpha)])

### Loading the data

In [5]:
#Loading the map cleaned of imaging shift and other basic corrections
dat = hs.load("clmap_IIB-HPHT-diamond_cleaned.hspy")

In [6]:
dat.axes_manager

<Axes manager, axes: (63, 64|875)>
            Name |   size |  index |  offset |   scale |  units 
================ | ====== | ====== | ======= | ======= | ====== 
           Width |     63 |      0 |       0 |     3.4 |     µm 
          Height |     64 |      0 |       0 |     3.4 |     µm 
---------------- | ------ | ------ | ------- | ------- | ------ 
      Wavelength |    875 |      0 | 2.1e+02 |   0.064 |     nm

In [7]:
#How to display the instrument metadata
dat.original_metadata

└── Object_0_Channel_0
    ├── Header
    │   ├── H01_Signature = DIGITAL SURF
    │   ├── H02_Format = 0
    │   ├── H03_Number_of_Objects = 1
    │   ├── H04_Version = 1
    │   ├── H05_Object_Type = 21
    │   ├── H06_Object_Name = HYPCard
    │   ├── H07_Operator_Name = 
    │   ├── H08_P_Size = 1
    │   ├── H09_Acquisition_Type = 0
    │   ├── H10_Range_Type = 0
    │   ├── H11_Special_Points = 0
    │   ├── H12_Absolute = 1
    │   ├── H13_Gauge_Resolution = 0.0
    │   ├── H14_W_Size = 1024
    │   ├── H15_Size_of_Points = 32
    │   ├── H16_Zmin = 0
    │   ├── H17_Zmax = 65535
    │   ├── H18_Number_of_Points = 64
    │   ├── H19_Number_of_Lines = 64
    │   ├── H20_Total_Nb_of_Pts = 4096
    │   ├── H21_X_Spacing = 2.0885674953460693
    │   ├── H22_Y_Spacing = 2.0885674953460693
    │   ├── H23_Z_Spacing = 1.0
    │   ├── H24_Name_of_X_Axis = Width
    │   ├── H25_Name_of_Y_Axis = Height
    │   ├── H26_Name_of_Z_Axis = CL Intensity
    │   ├── H27_X_Step_Unit = um
    │   ├── H28_Y_Step_Unit = um
    │   ├── H29_Z_Step_Unit = a.u.
    │   ├── H30_X_Length_Unit = um
    │   ├── H31_Y_Length_Unit = um
    │   ├── H32_Z_Length_Unit = a.u.
    │   ├── H33_X_Unit_Ratio = 1.0
    │   ├── H34_Y_Unit_Ratio = 1.0
    │   ├── H35_Z_Unit_Ratio = 1.0
    │   ├── H36_Imprint = 0
    │   ├── H37_Inverted = 0
    │   ├── H38_Levelled = 0
    │   ├── H39_Obsolete = b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'
    │   ├── H40_Seconds = 0
    │   ├── H41_Minutes = 0
    │   ├── H42_Hours = 0
    │   ├── H43_Day = 0
    │   ├── H44_Month = 0
    │   ├── H45_Year = 0
    │   ├── H46_Day_of_week = 0
    │   ├── H47_Measurement_duration = 2048.0
    │   ├── H48_Compressed_data_size = 0
    │   ├── H49_Obsolete = b'\x00\x00\x00\x00\x00\x00'
    │   ├── H50_Comment_size = 2664
    │   ├── H51_Private_size = 0
    │   ├── H52_Client_zone =                                                                                                                                 
    │   ├── H53_X_Offset = 0.0
    │   ├── H54_Y_Offset = 0.0
    │   ├── H55_Z_Offset = 0.0
    │   ├── H56_T_Spacing = 0.06405988335609436
    │   ├── H57_T_Offset = 202.09552001953125
    │   ├── H58_T_Axis_Name = Wavelength
    │   ├── H59_T_Step_Unit = nm
    │   └── H60_Comment = $_WAFER
$Lot Number=LOT_0000
$ID=WAFER_0000
$Type=ROUNDWITHFLAT
$Center Positi ... 12
$Start_Y=0
$Size_Y=512
$Rotate=311.000000 deg
$InitialRotate=180.000000 deg
    └── Parsed
        ├── CCD
        │   ├── Baseline Clamp = Off
        │   ├── Camera Model = A.920
        │   ├── Capture Depth = 1024
        │   ├── Exposure Time = 0.5
        │   ├── Exposure Time_units = s
        │   ├── Horizontal Binning = 1
        │   ├── Pixel Width = 0.026
        │   ├── Pixel Width_units = mm
        │   ├── ReadMode = FVB
        │   ├── Readout Rate (horizontal pixel shift) = 50Khz
        │   ├── Signal Amplification = x4
        │   ├── Speed (vertical pixel shift) = 1.7
        │   ├── Temperature = -69
        │   ├── Temperature_units = °C
        │   └── Voltage Amplitude (vertical pixel shift) = normal
        ├── CHANNELS
        │   ├── Channel1 = SE
        │   └── Channel2 = CCD
        ├── SCAN
        │   ├── HYP Dwelltime = 500.0
        │   ├── HYP Dwelltime_units = ms
        │   ├── InitialRotate = 180.0
        │   ├── InitialRotate_units = deg
        │   ├── Mode = HYP
        │   ├── Reference_Size_X = 512
        │   ├── Reference_Size_Y = 512
        │   ├── Resolution_X = 64
        │   ├── Resolution_X_units = pixels
        │   ├── Resolution_Y = 64
        │   ├── Resolution_Y_units = pixels
        │   ├── Rotate = 311.0
        │   ├── Rotate_units = deg
        │   ├── Size_X = 512
        │   ├── Size_Y = 512
        │   ├── Start_X = 0
        │   ├── Start_Y = 0
        │   ├── Voltage Calibration Range_X = 9.2
        │   ├── Voltage Calibration Range_X_units = V
        │   ├── Voltage Calibration Range_Y = 9.2
        │   └── Voltage Calibration Range_Y_u

In [7]:
dat.plot(norm='linear')

In [9]:
plt.close('all')

## Signal Variance Computation

### First step: PCA decomposition

PCA decomposition, creation of data and residue signal objects

Number of significant components are estimated from hyperspy's standard method to find knee of scree plot.

See https://ieeexplore.ieee.org/document/5961514

In [8]:
#PCA decomposition
dat.decomposition()
#Creation of the PCA signal map
PCA_signal_map = dat.get_decomposition_model(dat.learning_results.number_significant_components)
#Creation of the PCA noise map
PCA_noise_map = dat-PCA_signal_map

Decomposition info:
  normalize_poissonian_noise=False
  algorithm=SVD
  output_dimension=None
  centre=None


### Second step: 2d signal vs noise histogram

In [9]:
#Unit bins range.Integer bins between min and max of all data
Xbin = np.arange(0,int(PCA_signal_map.data.max()))
Ybin = np.arange(int(PCA_noise_map.data.min()),int(PCA_noise_map.data.max()))

#Plotting the histogram
fig = plt.figure()

heatmap, xedges, yedges,img = plt.hist2d(PCA_signal_map.data.ravel(),
                              PCA_noise_map.data.ravel(),
                              bins=(Xbin,Ybin),
                              norm=SymLogNorm(linthresh=1.0,vmin=0,vmax=1e4),
                              density=False
                             )

plt.colorbar(mappable=img,ticks=(0,1,1e1,1e2,1e3,1e4,1e5),label='Occurences')
fig.set_size_inches((220/25.4,100/25.4))
plt.xlabel('PCA Signal [Counts]')
plt.ylabel('PCA Noise  [Counts]')
plt.tight_layout()

In [10]:
#Storing the histogram as a hyperspy signal1D object, ie as a serie of 1d histogram. 
#Other solutions are naturally possible, but I found this to be the easiest.

#Formatting some nice axes
xax = {'name': 'Signal Intensity (counts)',
  'units': 'au',
  'navigate': True,
  'size': len(xedges)-1,
  'scale': np.diff(xedges)[0],
  'offset': 0.5*(xedges[0]+xedges[1])}
yax = {'name': 'PCA_noise_map',
  'units': 'au',
  'navigate': False,
  'size': len(yedges)-1,
  'scale': np.diff(yedges)[0],
  'offset': 0.5*(yedges[0]+yedges[1])}
#Signal initialisation
hist2ddata = hs.signals.Signal1D(heatmap,axes=[xax,yax])

### Third step: Pseudo-photon-transfer-curve of the data

In [11]:
#Computation of the Pseudo-photon-transfer-curve with confidence intervals

#We do not use signal levels where less than 10 histogram points are available
mids = hist2ddata.axes_manager.signal_axes[0].axis
pseudo_PTC = hist2ddata.map(function=hist_var,show_progressbar=False,inplace=False,mids=mids,minpoints=10)

#Confidence intervals computation using chi squared interval evaluation.
confint_var = hist2ddata.map(function=hist_var_confint,show_progressbar=False,inplace=False,mids=mids,minpoints=10)
confint_var.axes_manager.signal_axes[0].offset = 2.5
confint_var.axes_manager.signal_axes[0].scale = 95
confint_var.axes_manager.signal_axes[0].name = 'confidence'
confint_var.axes_manager.signal_axes[0].units = '%'

In [12]:
#Relative uncertainty of the variance estimation computed from the confidence interval
rel_unc = (confint_var-pseudo_PTC)/pseudo_PTC

#Setting a threshold for the fit range. 25% is a good value
threshold = 0.25
#We exclude from the fit data from the first point it exceeds the uncertainty threshold
start = 0
stop = np.min(np.argmax(((rel_unc<-1*threshold)+(rel_unc>threshold)).data,axis=0))

#Fit of the affine model on the Pseudo-PTC
x = pseudo_PTC.axes_manager.navigation_axes[0].axis
y = pseudo_PTC.data
poly = np.polyfit(x[start:stop],y[start:stop],1)

print(f"fit range stop: {stop} counts. Fit result: var = {poly[0]:.3f}*counts + {poly[1]:.0f}")

fit range stop: 246 counts. Fit result: var = 0.458*counts + 23


Custom plot of the pseudo-ptc with confidence interval

In [13]:
plt.figure()

plt.loglog(x,y,'k.',label='data',markersize=1)
plt.fill_between(x,confint_var.data[:,1],confint_var.data[:,0],label='95% confidence interval')

plt.plot(x[start:stop],np.polyval(poly,x[start:stop]),
         '-',color='darkgreen',linewidth=1.5,
         label = f'fit: {poly[0]:.2f} Signal + {poly[1]:.0f}')

plt.plot(x[stop:],np.polyval(poly,x[stop:]),
         '-',color='darkred',linewidth=1.5,label='fit extension'
        )

plt.legend()
plt.ylabel('Variance (Counts)')
plt.xlabel('Signal (Counts)')
plt.xlim(1,1300)
plt.ylim(10,1000)
plt.tight_layout()

### Fourth step: Creation of the variance map
Fitting an affine model on the data

In [14]:
#Creation of the variance map object
varmap = PCA_signal_map.deepcopy()*poly[0] + poly[1]
varmap.metadata.General.title = "Variance map"
varmap.metadata.Signal.quantity = "sigma**2 [au]"

The variance map is a hyperspy object with the same dimensions as the signal object: it indicates us the variance of the detected signal at each wavelength channel of each pixel. Counts measurements std map can be obtained with: `varmap**0.5`

In [15]:
varmap.axes_manager

<Axes manager, axes: (63, 64|875)>
            Name |   size |  index |  offset |   scale |  units 
================ | ====== | ====== | ======= | ======= | ====== 
           Width |     63 |      0 |       0 |     3.4 |     µm 
          Height |     64 |      0 |       0 |     3.4 |     µm 
---------------- | ------ | ------ | ------- | ------- | ------ 
      Wavelength |    875 |      0 | 2.1e+02 |   0.064 |     nm

In [18]:
varmap.plot()

## Conversion to eV, setting the variance property of the signal

Here a new signal is computed from the original one. A functional axis is built through $ hc/\lambda $, intensity values are renormalized through the jacobian of the variable change so that the integral of the signal is preserved

In [23]:
ax = dat.axes_manager.signal_axes[0]

In [24]:
from scipy import constants as cst
hc = cst.h*cst.c/cst.e*1e9   #hc product in nm/eV
hc

1239.8419843320025

In [25]:
#Creating a copy of the data object
sev = dat.deepcopy()
#Changing the axis of the copy
sev.axes_manager.signal_axes[0].convert_to_functional_data_axis(\
                                                          expression="a/x",
                                                          name='Energy',
                                                          units='eV',
                                                          a=hc,
                                                          )
#Reverting the orientation of signal to have increasing Energy
sev = sev.isig[::-1]
#Jacobian transformation
Eax = sev.axes_manager.signal_axes[0].axis
sev *= hc/Eax**2

Plot of the eV signal

In [26]:
sev.plot()

c:\users\nicolastappy\documents\git\hyperspy\hyperspy\signal.py:3702: UserWarning: You are summing over an unbinned, non-uniform axis. The result can not be used as an approximation of the integral of the signal. For this functionality, use integrate1D instead.
  warnings.warn("You are summing over an unbinned, non-uniform axis. "


The variance map is also converted to eV, but there the intensities have to be multiplied by the square of the jacobian according to
${\rm Var}(aX) = a^2{\rm Var}(X) $

In [27]:
sev_varmap = sev._deepcopy_with_new_data(varmap.isig[::-1].data*(hc/Eax**2)**2)

In [28]:
sev_varmap.plot()

c:\users\nicolastappy\documents\git\hyperspy\hyperspy\signal.py:3702: UserWarning: You are summing over an unbinned, non-uniform axis. The result can not be used as an approximation of the integral of the signal. For this functionality, use integrate1D instead.
  warnings.warn("You are summing over an unbinned, non-uniform axis. "


Variance properties of the whole map can then be set. In hyperspy, they will automatically be used as weights for the fit

In [29]:
sev.estimate_poissonian_noise_variance(sev_varmap)

In [30]:
sev.metadata.Signal.Noise_properties

├── Variance_linear_model
│   ├── correlation_factor = 1
│   ├── gain_factor = 1
│   └── gain_offset = 0
└── variance = <BaseSignal, title: Variance of , dimensions: (63, 64|875)>

In [31]:
sev.save('clmap_IIB-HPHT-diamond_eV_with_variance.hspy')

In [32]:
plt.close('all')